In [3]:
import pandas as pd
import numpy as np
import os
import pickle
from pandas.tseries.offsets import MonthEnd
from Main import settings, features, pf_set
from datetime import datetime
import portfolio_choice_functions
import General_Functions
import prepare_portfolio_data
import data_run_files
import Estimate_Covariance_Matrix
import Prepare_Data
import Estimate_Covariance_Matrix as ECM
import Prepare_Data
from itertools import product
import matplotlib.pyplot as plt
import seaborn as sns
# Path to save the portfolios.
output_path = "./data_fifty/"


# indhent barra_cov
barra_cov = ECM.main()
# indhent wealth
#wealth = Prepare_Data.main()
#wealth = wealth.dropna(subset=['wealth'])

chars, lambda_list, first_cov_date, hp_years, start_oos, date_ranges, risk_free = prepare_portfolio_data.main(barra_cov)
dates_m1 = date_ranges["dates_m1"]
dates_m2 = date_ranges["dates_m2"]
dates_oos = date_ranges["dates_oos"]
dates_hp = date_ranges["dates_hp"]


All missing excludes 39.99% of the observations
Filen er indlæst og filtreret succesfuldt.
No size screen
Turnover wo addition/deletion rule: 0.44%
Turnover w  addition/deletion rule: 2.35%


Processerer datoer: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 338/338 [00:03<00:00, 105.26it/s]


Filtrering udført. Antal rækker efter filtrering: 179
Fil gemt som ./data_test/risk_free_test.csv
All missing excludes 42.07% of the observations
All missing excludes 41.17% of the observations
Filen er indlæst og filtreret succesfuldt.
No size screen
Turnover wo addition/deletion rule: 0.28%
Turnover w  addition/deletion rule: 25.42%


In [7]:
dates_m1

DatetimeIndex(['2000-12-31', '2001-01-31', '2001-02-28', '2001-03-31',
               '2001-04-30', '2001-05-31', '2001-06-30', '2001-07-31',
               '2001-08-31', '2001-09-30',
               ...
               '2022-02-28', '2022-03-31', '2022-04-30', '2022-05-31',
               '2022-06-30', '2022-07-31', '2022-08-31', '2022-09-30',
               '2022-10-31', '2022-11-30'],
              dtype='datetime64[ns]', length=264, freq='ME')

In [6]:
dates_m2

DatetimeIndex(['1995-10-31', '1995-11-30', '1995-12-31', '1996-01-31',
               '1996-02-29', '1996-03-31', '1996-04-30', '1996-05-31',
               '1996-06-30', '1996-07-31',
               ...
               '2022-02-28', '2022-03-31', '2022-04-30', '2022-05-31',
               '2022-06-30', '2022-07-31', '2022-08-31', '2022-09-30',
               '2022-10-31', '2022-11-30'],
              dtype='datetime64[ns]', length=326, freq='ME')

In [9]:
ates_oos

DatetimeIndex(['2010-12-31', '2011-01-31', '2011-02-28', '2011-03-31',
               '2011-04-30', '2011-05-31', '2011-06-30', '2011-07-31',
               '2011-08-31', '2011-09-30',
               ...
               '2022-02-28', '2022-03-31', '2022-04-30', '2022-05-31',
               '2022-06-30', '2022-07-31', '2022-08-31', '2022-09-30',
               '2022-10-31', '2022-11-30'],
              dtype='datetime64[ns]', length=144, freq='ME')

In [10]:
dates_hp

DatetimeIndex(['2000-12-31', '2001-01-31', '2001-02-28', '2001-03-31',
               '2001-04-30', '2001-05-31', '2001-06-30', '2001-07-31',
               '2001-08-31', '2001-09-30',
               ...
               '2022-02-28', '2022-03-31', '2022-04-30', '2022-05-31',
               '2022-06-30', '2022-07-31', '2022-08-31', '2022-09-30',
               '2022-10-31', '2022-11-30'],
              dtype='datetime64[ns]', length=264, freq='ME')

In [4]:
barra_cov

{'1994-10-31': {'fct_load':        BusEq  Chems  Durbl  Enrgy  Hlth  Manuf  Money  NoDur  Other  Shops  \
  id                                                                           
  10104    1.0    0.0    0.0    0.0   0.0    0.0    0.0    0.0    0.0    0.0   
  10107    1.0    0.0    0.0    0.0   0.0    0.0    0.0    0.0    0.0    0.0   
  10138    0.0    0.0    0.0    0.0   0.0    0.0    1.0    0.0    0.0    0.0   
  10696    1.0    0.0    0.0    0.0   0.0    0.0    0.0    0.0    0.0    0.0   
  11308    0.0    0.0    0.0    0.0   0.0    0.0    0.0    1.0    0.0    0.0   
  ...      ...    ...    ...    ...   ...    ...    ...    ...    ...    ...   
  76712    0.0    0.0    0.0    0.0   0.0    0.0    0.0    0.0    1.0    0.0   
  78045    0.0    0.0    1.0    0.0   0.0    0.0    0.0    0.0    0.0    0.0   
  85914    0.0    0.0    0.0    0.0   0.0    0.0    0.0    0.0    0.0    1.0   
  87717    0.0    0.0    0.0    0.0   0.0    0.0    0.0    0.0    1.0    0.0   
  92655    0.0

## Hjælpefunktioner

In [16]:
# Portfolio Function
def sigma_gam_adj(sigma_gam, g, cov_type):
    if cov_type == "cov_mult":
        return sigma_gam * g
    elif cov_type == "cov_add":
        return sigma_gam + np.diag(np.diag(sigma_gam) * g)
    elif cov_type == "cor_shrink":
        if abs(g) > 1:
            raise ValueError("g must be between -1 and 1")
        sd_vec = np.sqrt(np.diag(sigma_gam))
        sd_vec_inv = np.linalg.inv(np.diag(sd_vec))
        cor_mat = sd_vec_inv @ sigma_gam @ sd_vec_inv
        cor_mat_adj = cor_mat * (1 - g) + np.eye(len(cor_mat)) * g
        return np.diag(sd_vec) @ cor_mat_adj @ np.diag(sd_vec)

        
# Create covariance matrix
def create_cov(x, ids=None):
    if ids is None:
        load = x['fct_load']
        ivol = x['ivol_vec']
    else:
        # Konverter ids til strings
        ids = pd.Index(ids).astype(str)
        load = x['fct_load'].loc[ids]
        ivol = x['ivol_vec'].loc[ids]
    return load @ x['fct_cov'] @ load.T + np.diag(ivol)

In [17]:

# Initial weights
def initial_weights_new(data, w_type, udf_weights=None):
    """
    Beregner initiale vægte baseret på w_type.

    Parametre:
      - data: Pandas DataFrame med mindst kolonnerne 'id', 'eom' og (afhængigt af w_type) 'me'
      - w_type: str, en af "vw", "ew", "rand_pos" eller "udf"
      - udf_weights: DataFrame med brugerdefinerede vægte (bruges, hvis w_type == "udf")

    Returnerer:
      - pf_w: DataFrame med kolonnerne 'id', 'eom', 'w_start' og 'w'
    """
    # Lav en kopi af data for at undgå sideeffekter
    df = data.copy()

    if w_type == "vw":
        # For hver eom beregnes w_start som me divideret med summen af me i gruppen
        df['w_start'] = df.groupby('eom')['me'].transform(lambda x: x / x.sum())
        pf_w = df[['id', 'eom', 'w_start']].copy()

    elif w_type == "ew":
        # For hver eom sættes w_start = 1 / antal elementer i gruppen
        df['w_start'] = df.groupby('eom')['id'].transform(lambda x: 1 / len(x))
        pf_w = df[['id', 'eom', 'w_start']].copy()

    elif w_type == "rand_pos":
        # Vælg kun de relevante kolonner
        pf_w = df[['id', 'eom']].copy()
        # Generér tilfældige tal for hver række
        pf_w['w_start'] = np.random.uniform(0, 1, size=len(pf_w))
        # Normalisér inden for hver eom, så summen af w_start = 1
        pf_w['w_start'] = pf_w.groupby('eom')['w_start'].transform(lambda x: x / x.sum())

    elif w_type == "udf":
        if udf_weights is None:
            raise ValueError("udf_weights skal angives, når w_type er 'udf'")
        # Merge udf_weights med data på id og eom
        # Her antages det, at udf_weights indeholder kolonnen 'w_start'
        pf_w = pd.merge(data[['id', 'eom']], udf_weights, on=['id', 'eom'], how='left')

    else:
        raise ValueError("Ugyldigt w_type angivet.")

    # For alle rækker, hvor eom ikke er den mindste (tidligste) dato, sættes w_start til NaN
    min_eom = pf_w['eom'].min()
    pf_w.loc[pf_w['eom'] != min_eom, 'w_start'] = np.nan

    # Tilføj kolonnen 'w' og sæt den til NaN for alle rækker
    pf_w['w'] = np.nan

    return pf_w

In [28]:

#Static Validation
def static_val_fun(data, dates, cov_list, lambda_list, wealth, cov_type, gamma_rel, k=None, g=None, u=None, hps=None):
    static_weights = initial_weights_new(data, w_type="vw")
    static_weights = pd.merge(static_weights, data[["id", "eom", "tr_ld1", "pred_ld1"]], on=["id", "eom"], how="left")
    static_weights = pd.merge(static_weights, wealth[["eom", "mu_ld1"]], on="eom", how="left")

    for d in dates:

        if hps is not None:
            # Filtrer alle hyperparametre med eom_ret < d
            hp_filtered = hps[hps["eom_ret"] < pd.Timestamp(d)]
            if not hp_filtered.empty:
                # Vælg den række med den højeste eom_ret (dvs. den seneste før d)
                hp = hp_filtered.loc[hp_filtered["eom_ret"].idxmax()]
                g = hp["g"]
                u = hp["u"]
                k = hp["k"]
            else:
                continue

        wealth_t = wealth.loc[wealth["eom"] == pd.Timestamp(d), "wealth"].values[0]
        ids = static_weights.loc[static_weights["eom"] == pd.Timestamp(d), "id"]

        # Konverter d til en streng nøgle, fx "2019-12-31"
        key = pd.Timestamp(d).strftime('%Y-%m-%d')
        sigma_gam = create_cov(cov_list[key], ids) * gamma_rel
        sigma_gam = sigma_gam_adj(sigma_gam, g, cov_type)

        id_list = list(ids)
        lambda_vals = [lambda_list[key][i] for i in id_list]
        lambda_matrix = np.diag(lambda_vals) * k

        weights = np.linalg.solve(
            sigma_gam + wealth_t * lambda_matrix,
            (u * static_weights.loc[static_weights["eom"] == pd.Timestamp(d), "pred_ld1"] +
             wealth_t * lambda_matrix @ static_weights.loc[static_weights["eom"] == pd.Timestamp(d), "w_start"])
        )

        static_weights.loc[static_weights["eom"] == pd.Timestamp(d), "w"] = weights

        next_index = dates.get_loc(d) + 1
        next_month = dates[next_index] if next_index < len(dates) else None
        if next_month:
            mask_current = static_weights["eom"] == pd.Timestamp(d)
            mask_next = static_weights["eom"] == pd.Timestamp(next_month)
            current_tr = static_weights.loc[mask_current, "tr_ld1"].values
            current_mu = static_weights.loc[mask_current, "mu_ld1"].values
            next_weights = weights * (1 + current_tr) / (1 + current_mu)
            static_weights.loc[mask_next, "w_start"] = next_weights
            static_weights.loc[:, "w_start"] = static_weights["w_start"].fillna(0)

    return static_weights

In [29]:
print("dates_m1", dates_m1)
print("dates_m2",dates_m2)
print("dates_oos",dates_oos)
print("dates_hp", dates_hp) 

dates_m1 DatetimeIndex(['2015-12-31', '2016-01-31', '2016-02-29', '2016-03-31',
               '2016-04-30', '2016-05-31', '2016-06-30', '2016-07-31',
               '2016-08-31', '2016-09-30', '2016-10-31', '2016-11-30',
               '2016-12-31', '2017-01-31', '2017-02-28', '2017-03-31',
               '2017-04-30', '2017-05-31', '2017-06-30', '2017-07-31',
               '2017-08-31', '2017-09-30', '2017-10-31', '2017-11-30',
               '2017-12-31', '2018-01-31', '2018-02-28', '2018-03-31',
               '2018-04-30', '2018-05-31', '2018-06-30', '2018-07-31',
               '2018-08-31', '2018-09-30', '2018-10-31', '2018-11-30',
               '2018-12-31', '2019-01-31', '2019-02-28', '2019-03-31',
               '2019-04-30', '2019-05-31', '2019-06-30', '2019-07-31',
               '2019-08-31', '2019-09-30', '2019-10-31', '2019-11-30',
               '2019-12-31', '2020-01-31', '2020-02-29', '2020-03-31',
               '2020-04-30', '2020-05-31', '2020-06-30', '2020-07-31

In [22]:

def pf_ts_fun(weights, data, wealth, gam):
    # Join weights med relevante data-kolonner (id, eom, ret_ld1, pred_ld1, lambda)
    data_subset = data[['id', 'eom', 'ret_ld1', 'pred_ld1', 'lambda']]
    comb = pd.merge(weights, data_subset, on=['id', 'eom'], how='left')

    # Join med wealth for at tilføje 'wealth'-kolonnen (join på eom)
    wealth_subset = wealth[['eom', 'wealth']]
    comb = pd.merge(comb, wealth_subset, on='eom', how='left')

    # Aggregér porteføljestatistikker pr. eom
    def agg_func(g):
        inv = np.sum(np.abs(g['w']))
        shorting = np.sum(np.abs(g.loc[g['w'] < 0, 'w']))
        turnover = np.sum(np.abs(g['w'] - g['w_start']))
        r = np.sum(g['w'] * g['ret_ld1'])
        # For tc antages det, at der er et unikt wealth pr. eom
        unique_wealth = g['wealth'].unique()[0] if len(g['wealth'].unique()) > 0 else np.nan
        tc = (unique_wealth / 2) * np.sum(g['lambda'] * ((g['w'] - g['w_start']) ** 2))
        return pd.Series({
            'inv': inv,
            'shorting': shorting,
            'turnover': turnover,
            'r': r,
            'tc': tc
        })

    #pf = comb.groupby('eom').apply(agg_func).reset_index()
    pf = comb.groupby('eom').apply(agg_func, include_groups=False).reset_index()


    # Udregn eom_ret som eom plus 1 måned (forudsætter at eom er en datetime)
    pf['eom'] = pd.to_datetime(pf['eom'])
    pf['eom_ret'] = pf['eom'] + pd.DateOffset(months=1)

    # Fjern den oprindelige eom-kolonne, hvis ønsket
    pf = pf.drop(columns=['eom'])

    return pf

# Final Static Implemtation funktion

In [1]:
#Static Full Implementation
def static_implement(data_tc, cov_list, lambda_list, rf,
                     wealth, mu, gamma_rel,
                     dates_full, dates_oos, dates_hp, hp_years,
                     k_vec, u_vec, g_vec, cov_type,
                     validation=None, seed=None):
    data_tc = data_tc[(data_tc['valid'] == True) & (data_tc['eom'].isin(dates_oos))].copy()
    dates_hp = dates_hp[dates_hp >= pd.Timestamp(dates_oos[0].strftime('%Y-%m-%d'))]
    # Sæt seed, hvis nødvendigt
    if seed is not None:
        np.random.seed(seed)

    # HP grid: opret en DataFrame med alle kombinationer af k, u og g
    static_hps = pd.DataFrame(list(product(k_vec, u_vec, g_vec)), columns=['k', 'u', 'g'])

    # Udvælg relevant data: filter på 'valid' == True og eom i dates_hp og sorter efter id og eom
    data_rel = (data_tc.loc[(data_tc['valid']) & (data_tc['eom'].isin(dates_hp)),
    ['id', 'eom', 'me', 'tr_ld1', 'pred_ld1']]
                .sort_values(by=['id', 'eom'])
                )

    # Validering: Hvis validation er None, beregn den
    if validation is None:
        validation_list = []
        for i in range(len(static_hps)):
            print(i)
            # Hent hyperparameterkombinationen
            hp = static_hps.iloc[i]
            # Kald funktionen static_val_fun på data_rel med de aktuelle hyperparametre
            static_w = static_val_fun(data_rel, dates=dates_hp, cov_list=cov_list,
                                      lambda_list=lambda_list, wealth=wealth, gamma_rel=gamma_rel,
                                      k=hp['k'], g=hp['g'], u=hp['u'], cov_type=cov_type)
            # Kald herefter pf_ts_fun på static_w og tilføj kolonner med hyperparametre og hp-nummer
            pf = pf_ts_fun(static_w, data=data_tc, wealth=wealth, gam=gamma_rel)
            pf = pf.copy()  # For at undgå advarsler om SettingWithCopy
            pf['hp_no'] = i
            pf['k'] = hp['k']
            pf['g'] = hp['g']
            pf['u'] = hp['u']
            validation_list.append(pf)

        # Kombinér resultaterne til én DataFrame (svarer til rbindlist)
        validation = pd.concat(validation_list, ignore_index=True)

    # Sorter validation efter hp_no og eom_ret
    validation.sort_values(by=['hp_no', 'eom_ret'], inplace=True)

    # Beregn kumulativ varians: cum_var = cummean(r^2) - (cummean(r))^2, beregnet pr. hp_no-gruppe
    validation['cum_var'] = (validation
                             .groupby('hp_no')['r']
                             .apply(lambda x: (x.pow(2).expanding().mean() - x.expanding().mean().pow(2)))
                             .reset_index(level=0, drop=True)
                             )

    # Beregn kumulativ objektiv funktion: cum_obj = cummean(r - tc - 0.5*cum_var*gamma_rel) pr. hp_no
    validation['cum_obj'] = (validation
                             .groupby('hp_no')
                             .apply(lambda group: (group['r'] - group['tc'] - 0.5 * group['cum_var'] * gamma_rel)
                                    .expanding().mean())
                             .reset_index(level=0, drop=True)
                             )

    # Beregn rang inden for hver eom_ret: højere cum_obj giver lavere rang (rank 1 er bedst)
    validation['rank'] = (validation
                          .groupby('eom_ret')['cum_obj']
                          .rank(ascending=False, method='min')
                          )

    # Plot: opret en 'name'-kolonne og filtrér for år >= 1981
    validation = validation.copy()
    validation['name'] = ("u:" + validation['u'].astype(str) +
                          " k:" + validation['k'].round(2).astype(str) +
                          " g:" + validation['g'].astype(str))

    plot_df = validation[validation['eom_ret'].dt.year >= 1981].copy()
    # For hver hp_no, beregn minimum rank og filtrér for dem med min_rank <= 1
    plot_df['min_rank'] = plot_df.groupby('hp_no')['rank'].transform('min')
    plot_df_filtered = plot_df[plot_df['min_rank'] <= 1]

    # Lav plot med seaborn
#    plt.figure(figsize=(10, 6))
#    sns.lineplot(data=plot_df_filtered, x='eom_ret', y=plot_df_filtered['cum_obj'] * 12, hue='name')
#    plt.xlabel('eom_ret')
#    plt.ylabel('Kumulativ objektiv funktion * 12')
#    plt.title('Static-implement: Kumulativ objektiv funktion pr. hyperparameter')
#    plt.show()

    # Find optimale hyperparametre: vælg rækker med eom_ret i december og rank==1
    optimal_hps = (validation[(validation['eom_ret'].dt.month == 12) & (validation['rank'] == 1)]
                   .sort_values(by='eom_ret'))

    # Implementer det endelige portfolio:
    # Udvælg data_tc for datoer i dates_oos og hvor valid==True
    w_data = data_tc.loc[(data_tc['valid']) & (data_tc['eom'].isin(dates_oos)),
    ['id', 'eom', 'me', 'tr_ld1', 'pred_ld1']]
    w = static_val_fun(w_data, dates=dates_oos, cov_list=cov_list, lambda_list=lambda_list,
                       wealth=wealth, gamma_rel=gamma_rel, hps=optimal_hps, cov_type=cov_type)

    # Beregn portefølje-tidsserie og tilføj en 'type'-kolonne
    pf = pf_ts_fun(w, data=data_tc, wealth=wealth, gam=gamma_rel)
    pf = pf.copy()
    pf['type'] = "Static-ML*"

    # Returnér resultaterne som en ordbog
    return {"hps": validation, "best_hps": optimal_hps, "w": w, "pf": pf}

In [2]:
static = static_implement(
    data_tc=chars,
    cov_list=barra_cov,
    lambda_list=lambda_list,
    rf=risk_free,              # Data
    wealth=wealth,
    mu=pf_set['mu'],
    gamma_rel=pf_set['gamma_rel'],  # Investor
    dates_full=dates_m1,
    dates_oos=dates_oos,
    dates_hp=dates_hp,
    hp_years=hp_years,          # Dates
    k_vec=settings['pf']['hps']['static']['k'],
    u_vec=settings['pf']['hps']['static']['u'],
    g_vec=settings['pf']['hps']['static']['g'],
    cov_type=settings['pf']['hps']['cov_type'],
    validation=None
)

NameError: name 'chars' is not defined

In [26]:
static

{'hps':            inv  shorting  turnover         r        tc    eom_ret  hp_no    k  \
 0     0.602167  0.023467  0.444766 -0.000534  0.001407 2020-01-31      0  1.0   
 1     0.486646  0.063525  0.196633 -0.035702  0.000262 2020-02-29      0  1.0   
 2     0.457107  0.106561  0.108553 -0.024823  0.000070 2020-03-29      0  1.0   
 3     0.402759  0.166525  0.189540 -0.002663  0.000178 2020-04-30      0  1.0   
 4     0.347078  0.149425  0.074104 -0.000751  0.000041 2020-05-30      0  1.0   
 ...        ...       ...       ...       ...       ...        ...    ...  ...   
 1264  1.558910  0.538276  0.333172  0.002285  0.001513 2023-07-30     26  0.2   
 1265  1.536427  0.515927  0.320105 -0.000312  0.001540 2023-08-31     26  0.2   
 1266  1.591636  0.525289  0.381948 -0.020108  0.002115 2023-09-30     26  0.2   
 1267  1.698215  0.561790  0.361568 -0.013834  0.002197 2023-10-30     26  0.2   
 1268  1.783206  0.594410  0.444811  0.034985  0.002488 2023-11-30     26  0.2   
 
       